In [1]:
import numpy as np
import pandas as pd

data_url = "C:\\Users\\Enrico\\Desktop\\INFORMATICA_TRIENNALE\\dispense informatica\\Terzo anno\\DataWebMining\\Progetto\\train.csv"
df = pd.read_csv(data_url)

from textblob import TextBlob
from nltk.corpus import stopwords
stopwords=set(stopwords.words('english'))

# Ritorna la lista di lemmi, ottenuti con gli opportuni POS tag
def lemmatize_with_postag(sentence):
    sent = TextBlob(sentence).lower()
    tag_dict = {"J": 'a', 
                "N": 'n', 
                "V": 'v', 
                "R": 'r'}
    words_and_tags = [(w, tag_dict.get(pos[0], 'n')) for w, pos in sent.tags]    
    lemmatized_list = [wd.lemmatize(tag) for wd, tag in words_and_tags]
    return lemmatized_list

In [2]:
df["overview"] = df["overview"].fillna("")

In [ ]:
df["overview"] = df["overview"].map(lambda s : lemmatize_with_postag(s))

In [ ]:
lexicon = set([])
for film in df.index.values:
    lexicon |= set(df.loc[film,"overview"])
lexicon = lexicon - stopwords

In [ ]:
lexicon_map     = {term:id for id,term in enumerate(lexicon)}
lexicon_rev_map = {id:term for term,id in lexicon_map.items()}

In [ ]:
len(lexicon)

In [ ]:
def get_vector_space (overviews, lex_map):
    m = np.zeros((max(overviews.index.values)+1, len(lex_map)))

    for film_id in range(len(m)):
        if film_id not in overviews.index.values:
            m[film_id,:] = -1
            continue
        for lem in overviews.loc[film_id]:
            if lem in lex_map:
                term_id = lex_map[lem]
                m[film_id,term_id] += 1.0 
    
    return m

vector_space = get_vector_space(df["overview"], lexicon_map)

In [62]:
print(df["overview"][0])
print(sum(vector_space[0]))
[lexicon_rev_map[id] for id in range(vector_space.shape[1]) if vector_space[0,id] >0.0 ]

['when', 'lou', 'who', 'have', 'become', 'the', 'father', 'of', 'the', 'internet', 'be', 'shoot', 'by', 'an', 'unknown', 'assailant', 'jacob', 'and', 'nick', 'fire', 'up', 'the', 'time', 'machine', 'again', 'to', 'save', 'their', 'friend']
14.0


['father',
 'lou',
 'machine',
 'become',
 'jacob',
 'nick',
 'fire',
 'unknown',
 'save',
 'friend',
 'time',
 'assailant',
 'internet',
 'shoot']

In [14]:
np.argmax(np.sum(vector_space,axis=1))
df.loc[156,"overview"]

['артем',
 'колчин',
 'был',
 'одним',
 'из',
 'многих',
 'но',
 'он',
 'хотел',
 'славы',
 'и',
 'он',
 'выбрал',
 'свой',
 'путь',
 'он',
 'стал',
 'боксером',
 'теперь',
 'артем',
 'претендент',
 'на',
 'чемпионский',
 'титул',
 'боец',
 'известный',
 'по',
 'всему',
 'миру',
 'большая',
 'белая',
 'надежда',
 'но',
 'главный',
 'бой',
 'в',
 'его',
 'жизни',
 'пошел',
 'не',
 'так',
 'как',
 'он',
 'ожидал',
 'теперь',
 'ему',
 'предстоит',
 'решать',
 'свои',
 'проблемы',
 'вне',
 'ринга',
 'у',
 'него',
 'всего',
 'три',
 'дня',
 'чтобы',
 'расквитаться',
 'с',
 'теми',
 'кто',
 'его',
 'предал',
 'защитить',
 'любимую',
 'женщину',
 'от',
 'наемных',
 'убийц',
 'и',
 'собрать',
 'огромную',
 'сумму',
 'денег',
 'в',
 'реальном',
 'мире',
 'бьют',
 'без',
 'перчаток',
 'и',
 'без',
 'правил',
 'вместо',
 'ринга',
 '—',
 'злые',
 'улицы',
 'большого',
 'города',
 'и',
 'нет',
 'рефери',
 'который',
 'может',
 'остановить',
 'бой',
 'но',
 'боец',
 'остается',
 'бойцом',
 'он',
 'з

In [22]:
print(np.sum(vector_space>0))
np.sum(vector_space==0)

84329


47555671

In [24]:
np.argwhere(np.array([1,2,3,4])>2).reshape((2,))

array([2, 3], dtype=int64)

In [27]:
np.argwhere(vector_space[:,1000]>0)

array([[ 700],
       [ 922],
       [ 985],
       [1025],
       [1039],
       [1268],
       [1333],
       [1418],
       [1843],
       [2465]], dtype=int64)

In [25]:
np.array([[1,2,3],[4,5,6],[7,8,9]])[ [True,True,False] ]

array([[1, 2, 3],
       [4, 5, 6]])

In [ ]:
similarity_vector = np.array([[-1 for j in range(vector_space.shape[0])] for i in range(vector_space.shape[0])])
for film_i in df.index.values:
    terms = np.argwhere(vector_space[film_i,:]>0)
    terms = terms.reshape((terms.shape[0],))
    for term in terms:
        films = np.argwhere(vector_space[:,term]>0)
        films = films.reshape((films.shape[0],))
        for film_j in films:
            if similarity_vector[film_i,film_j]<0:
                print(film_i,film_j,cosine(vector_space[film_i,:],vector_space[film_j,:]))
                similarity_vector[film_i,film_j] = cosine(vector_space[film_i,:],vector_space[film_j,:])
            



0 0 0.9999999999999998
0 2099 0.2040682695168364
0 1 0.009105141049322519
0 5 0.014195552305451812
0 8 0.009768006422311369
0 12 0.031947467635192586
0 15 0.007629097801488985
0 19 0.02316809931298142
0 23 0.019202222395743172
0 25 0.01642079342760585
0 27 0.007708098503678958
0 42 0.010217453653939088
0 56 0.005987796497175014
0 71 0.009537311851047186
0 108 0.01969808925965081
0 160 0.033663828991740787
0 162 0.011705518265351851
0 163 0.03172053446024902
0 188 0.008398191606308763
0 193 0.010149525909741193
0 194 0.013747294691350605
0 199 0.01331497129244107
0 225 0.008026709430719349
0 238 0.00761487062235269
0 245 0.02004501548465286
0 254 0.005660185631197304
0 262 0.0047749820882037036
0 265 0.009644302369977003
0 269 0.009518070037947657
0 271 0.008164362040456332
0 281 0.014747600360408258
0 293 0.008989653455560739
0 294 0.013735942963768897
0 312 0.010739843915596266
0 323 0.010156567548516788
0 349 0.02609238594729723
0 361 0.012167984464675489
0 388 0.02441460859335407
0 

0 850 0.022197069589436517
0 858 0.00842843169191437
0 866 0.004949496989755696
0 872 0.03564271427539314
0 873 0.02126286450089611
0 876 0.012997840240454958
0 887 0.021325505050746017
0 892 0.01334203953741973
0 897 0.00917923121554141
0 915 0.019558633768953598
0 927 0.022382961882015058
0 986 0.026291990812734825
0 995 0.0188721570137722
0 998 0.017698590209672137
0 1036 0.007683738375587281
0 1039 0.007706433033626815
0 1099 0.007260344016280314
0 1103 0.010742796071725477
0 1108 0.008195165427773475
0 1139 0.013758107671996962
0 1145 0.008791345650624349
0 1150 0.010943877817526154
0 1163 0.012687842216822936
0 1164 0.00782457021643621
0 1170 0.02847273691512632
0 1177 0.01728534385584025
0 1201 0.011152305125955428
0 1222 0.011169473004933927
0 1224 0.027242483123371068
0 1225 0.007464500516129773
0 1230 0.011598406839686895
0 1265 0.022206704846033837
0 1268 0.026818443584612665
0 1270 0.009790005951152193
0 1276 0.00931192833969965
0 1282 0.013709852820038986
0 1286 0.01477204

0 2387 0.014894059134516658
0 2400 0.0239563174284177
0 2402 0.013229591385277083
0 2408 0.01939954369310714
0 2425 0.013707054113772042
0 2441 0.03127851645988482
0 2461 0.009879443642256477
0 2471 0.009379440867767175
0 2511 0.006239649668271022
0 2528 0.01085605388437907
0 2533 0.007425754409047257
0 2543 0.015360457449346852
0 2571 0.011026663455000356
0 2590 0.007157482447822727
0 2594 0.020628637902382067
0 2595 0.036317247793362505
0 2629 0.009875513478476927
0 2631 0.01004005899300503
0 2647 0.009691314803317893
0 2685 0.01759346793990066
0 2687 0.008868940417712955
0 2739 0.03262967750264028
0 2754 0.018228501347934377
0 2756 0.016669957232141465
0 2778 0.011283668489118588
0 2821 0.012261922048891623
0 2824 0.0112615978587405
0 2879 0.04359037243325273
0 2880 0.029727187599216897
0 2929 0.02002379203577319
0 2981 0.025516478394937484
0 2982 0.010982662385732991
0 10 0.039554182756667215
0 22 0.05949814830649331
0 65 0.04582705753315338
0 234 0.03686136405815866
0 384 0.089793

1 542 0.024043056953858666
1 567 0.03325650240333907
1 577 0.019866265063023997
1 600 0.00525196653059234
1 613 0.062250814520160756
1 615 0.030482364087276403
1 623 0.008657014765721182
1 625 0.014549265956142057
1 634 0.004345410048946777
1 642 0.056100393801914124
1 656 0.009326924833940955
1 681 0.027862624120409255
1 695 0.007464281972536734
1 702 0.027356460169406967
1 715 0.008224288022660883
1 718 0.00434420428640027
1 725 0.01635522382979318
1 737 0.0182800706364189
1 754 0.010387040026764846
1 760 0.01300490986569953
1 764 0.011730723634156151
1 767 0.06062593196372594
1 768 0.006780306972925868
1 785 0.019396299672590243
1 786 0.01462298384393313
1 800 0.014097352868310592
1 804 0.010076736673384677
1 820 0.004842126099871129
1 847 0.006741372066013667
1 857 0.019875591187560597
1 860 0.013974831952632494
1 861 0.08232175572773909
1 879 0.013177619378026376
1 893 0.04944084784681311
1 902 0.004134931788215074
1 924 0.020371033393993505
1 951 0.03281153043683214
1 952 0.01240

1 512 0.026631341753280132
1 520 0.010268506659271493
1 570 0.007342099659384344
1 583 0.007177632182772429
1 604 0.013980728419663623
1 633 0.006458585038240659
1 645 0.02796164197616068
1 649 0.005520885056571625
1 722 0.007600459339349402
1 723 0.01869287628978058
1 746 0.010772832743297291
1 751 0.01402146334927186
1 763 0.007899006778227385
1 797 0.014118943540451817
1 814 0.006841514958236125
1 858 0.008141588082764472
1 872 0.011010797055116988
1 904 0.005320671301737428
1 926 0.009425264601737888
1 932 0.021098453181306105
1 941 0.0051008749127054555
1 985 0.013500325754432888
1 1035 0.011279422858198251
1 1049 0.004481606589935924
1 1057 0.009331698565388957
1 1068 0.02403770648277153
1 1081 0.014083948972537135
1 1085 0.011140997005481984
1 1105 0.025905125152134875
1 1165 0.010049236198082045
1 1166 0.011079085008714787
1 1168 0.04746284233272583
1 1174 0.007238852112041154
1 1205 0.015106626496327265
1 1217 0.005487492186573122
1 1225 0.012431268838810516
1 1226 0.010971519

...

161 1574 0.019943375090706296
161 1576 0.04127066571973179
161 1605 0.012664461241742158
161 1606 0.015412350786993049
161 1610 0.018012651187987793
161 1631 0.05443969816461466
161 1654 0.022255597725379897
161 1657 0.01157865784378069
161 1658 0.06259810075792611
161 1668 0.0445395414602605
161 1683 0.063995045924776
161 1691 0.03185447075298356
161 1701 0.004151196233522236
161 1702 0.00832538258283214
161 1716 0.018978937026655637
161 1735 0.014313357614341743
161 1748 0.02205038187667039
161 1751 0.006625838498188742
161 1753 0.01087969548134252
161 1770 0.01782460925121925
161 1771 0.004616328406536615
161 1795 0.006621061647736789
161 1796 0.009116702315652724
161 1819 0.014671395585049438
161 1820 0.010974762967641903
161 1828 0.0501129710696951
161 1836 0.010843775678041432
161 1849 0.020867732583673373
161 1854 0.047700655930770955
161 1878 0.0075812753447891115
161 1898 0.006019388977835521
161 1912 0.019204210272681335
161 1938 0.024941721561847822
161 1947 0.01272440555326

161 1030 0.013758434500472516
161 1035 0.013619875578360155
161 1052 0.012860628211219137
161 1055 0.022283284620830332
161 1088 0.00772756394281526
161 1108 0.017303951665935267
161 1122 0.010200624488512144
161 1141 0.020636458538668315
161 1178 0.0377350876948535
161 1179 0.008996894862471365
161 1180 0.006993834230449908
161 1188 0.005660632038149864
161 1216 0.030999010506739554
161 1217 0.006626133425260028
161 1232 0.026309022686414555
161 1251 0.05278970535164723
161 1279 0.006031199536813264
161 1306 0.014942173828773895
161 1326 0.019061400994147996
161 1338 0.039828127381386795
161 1348 0.020092027962796945
161 1385 0.006987942526229139
161 1401 0.009090471565182221
161 1415 0.00597537734696547
161 1438 0.005901642054989019
161 1444 0.024579674405330744
161 1451 0.007812535472308249
161 1459 0.012882407484142896
161 1463 0.05043767810033344
161 1464 0.007074986432066561
161 1517 0.01377484453199314
161 1566 0.008495900228392882
161 1577 0.01709585084901259
161 1580 0.0104436

161 770 0.03484777741695012
161 826 0.048411945638111416
161 887 0.031615196548708466
161 1021 0.05095150256720149
161 1027 0.07253730883269356
161 1228 0.07018467093590144
161 1262 0.034926273005953724
161 1362 0.019263222121010302
161 1368 0.03611142890855195
161 1409 0.07249824556189542
161 1414 0.050209118865771216
161 1425 0.0581632900475983
161 1453 0.043940304889401684
161 1481 0.030114216091832055
161 1487 0.04210750105583031
161 1516 0.04789887466148801
161 1551 0.04074827840170352
161 1599 0.07934423711011149
161 1692 0.030177352855061693
161 1763 0.03516298177136974
161 2037 0.048268761543796154
161 2122 0.04477220232181001
161 2156 0.0437986253087643
161 2219 0.07028620925763847
161 2345 0.05334671170239139
161 2378 0.0629683510225328
161 2387 0.051748847770378255
161 2396 0.04032144235065049
161 2418 0.03299654835588852
161 2432 0.030538222145885013
161 2465 0.0256188920830576
161 2490 0.07776042728883623
161 2613 0.037471067295805564
161 2664 0.044348338966451954
161 2669

161 1523 0.010471481262932718
161 1526 0.0039625343563176995
161 1531 0.0041528892812629555
161 1546 0.00915089616643734
161 1549 0.0075417552233714436
161 1554 0.004469423561509106
161 1561 0.004016533005579648
161 1581 0.0029416168977779767
161 1586 0.0059311305218950035
161 1607 0.011126510308849546
161 1649 0.013533584421808898
161 1651 0.003983631973398243
161 1667 0.015648729478197693
161 1673 0.00431195505714981
161 1674 0.005751639394152616
161 1678 0.023805959612748957
161 1679 0.006989867316361917
161 1681 0.013456102013360881
161 1695 0.009532495821863683
161 1706 0.004156281127409549
161 1708 0.005729305869190402
161 1711 0.013966818192172933
161 1712 0.007183512958233073
161 1742 0.003907538458098575
161 1743 0.0052054050009154905
161 1760 0.003930807674614255
161 1772 0.01594618177745737
161 1779 0.005926173560192561
161 1813 0.006064399697815111
161 1817 0.005881992645090028
161 1826 0.0046230860049069
161 1827 0.003024662421843664
161 1835 0.043748299440310875
161 1840 

161 2559 0.03353692517313886
161 2566 0.008650907806752296
161 2568 0.028784129292053838
161 2575 0.0053375772313077555
161 2577 0.01169804092703991
161 2605 0.02513586056992013
161 2639 0.006250779928725238
161 2659 0.009487173381789523
161 2680 0.012695494997026852
161 2712 0.022387664651004033
161 2730 0.00562694273017074
161 2744 0.007248346919088077
161 2753 0.013653139165446533
161 2767 0.008392272923926108
161 2779 0.012447864525136378
161 2784 0.005074753439311666
161 2787 0.013741779279781432
161 2812 0.0038432866941215628
161 2822 0.015134538352737772
161 2994 0.018900358499270336
161 102 0.024563390561138185
161 138 0.017508741054028207
161 277 0.012078561783763674
161 285 0.012810436040926357
161 292 0.01965275724396297
161 303 0.02613578349310235
161 341 0.024840406489053325
161 355 0.01780193478679846
161 358 0.009969408940670527
161 378 0.00942967083722519
161 384 0.01146002617523671
161 398 0.011533052853122141
161 404 0.019532448063696625
161 412 0.01919009068924581
16

In [ ]:
def scale_vector_space_by_idf(vector_space):
    Ndocs = len(vector_space)
    doc_freq = np.sum(vector_space>0,axis=0)
    return vector_space * np.log( Ndocs/doc_freq )

vector_space = scale_vector_space_by_idf(vector_space)

In [ ]:
def cosine(a,b):
    return np.dot(a,b)/( np.sqrt(np.sum(a**2.0)) * np.sqrt(np.sum(b**2.0)) )

In [ ]:
similarity_vector = np.array( [ [ (cosine(film_i,film_j) if ((film_i in df.index.values) and (film_j in df.index.values) and (film_i<film_j) and (sum(vector_space[film_i,:])>0) and (sum(vector_space[film_j,:])>0)) else np.NINF)  for film_j in range(len(vector_space))] for film_i in  range(len(vector_space))] )

<ipython-input-64-c05ebe146a5f>:2: RuntimeWarning: invalid value encountered in true_divide
  return np.dot(a,b)/( np.sqrt(np.sum(a**2.0)) * np.sqrt(np.sum(b**2)) )


In [ ]:
selected_films = [film_id for range(vector_space.shape[0]) if film_id in df.index.values and sum(vector_space[film_id,:])>0]

In [ ]:
similarity_vector = np.array([[-1.0 for j in range(len(vector_space))] for i in range(len(vector_space))])
for film_i in range(len(vector_space)):
    print(film_i)
    for film_j in range(film_i+1,len(vector_space)):
        similarity_vector[film_i,film_j] = cosine(vector_space[film_i,:],vector_space[film_j,:])
        #print(film_i,film_j,similarity_vector[film_i,film_j])

0


<ipython-input-11-766e32ad4d24>:2: RuntimeWarning: invalid value encountered in double_scalars
  return np.dot(a,b)/( np.sqrt(np.sum(a**2.0)) * np.sqrt(np.sum(b**2.0)) )


1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277


In [43]:
!pip install thread6

In [50]:
similarity_vector = None

Exception ignored in thread started byException ignored in thread started byException ignored in thread started by: : : <function f at 0x000001C909EE55E0>Exception ignored in thread started by: <function f at 0x000001C909EE55E0>
Traceback (most recent call last):
  File "<ipython-input-18-2166380919b3>", line 7, in f
<function f at 0x000001C91E18CE50><function f at 0x000001C91E18CE50>
Exception ignored in thread started by
: Traceback (most recent call last):
Traceback (most recent call last):

  File "<ipython-input-46-2166380919b3>", line 7, in f
Traceback (most recent call last):
  File "<ipython-input-46-2166380919b3>", line 7, in f
TypeErrorException ignored in thread started byTypeError<function f at 0x000001C909EE55E0>
Traceback (most recent call last):
Exception ignored in thread started byException ignored in thread started by  File "<ipython-input-18-2166380919b3>", line 7, in f
: : <function f at 0x000001C91E18CE50>:   File "<ipython-input-18-2166380919b3>", line 7, in f

'N

In [ ]:
from threading import Thread

similarity_vector = np.array([[-1.0 for j in range(len(vector_space))] for i in range(len(vector_space))])
def f(inf,sup):
    for film_i in range(inf,sup):
        print(film_i)
        for film_j in range(film_i+1,len(vector_space)):
           # if( film_i not in df.index.values or film_j not in df.index.values or sum(vector_space[film_i,:])<=0 or sum(vector_space[film_j,:]<=0)):
           #     continue
            similarity_vector[film_i,film_j] = cosine(vector_space[film_i,:],vector_space[film_j,:])
    print("FINITO")
    #_thread.exit()
"""_thread.start_new_thread( f, (0,600) )
_thread.start_new_thread( f, (600,1200) )
_thread.start_new_thread( f, (1200,1800) )
_thread.start_new_thread( f, (1800,2400) )
_thread.start_new_thread( f, (2400,3000) )"""
threads = []
t1 = Thread(target=f, args=(0,600))
t1.start()
threads.append(t1)
t2 = Thread(target=f, args=(600,1200))
t2.start()
threads.append(t2)
t3 = Thread(target=f, args=(1200,1800))
t3.start()
threads.append(t3)
t4 = Thread(target=f, args=(1800,2400))
t4.start()
threads.append(t4)
t5 = Thread(target=f, args=(2400,3000))
t5.start()
threads.append(t5)

for t in threads:
    t.join()


In [10]:
cosine(vector_space[0,:],vector_space[1,:])

0.009105141049322519

In [29]:
similarity_vector[0,1]

-1.0

<ipython-input-9-766e32ad4d24>:2: RuntimeWarning: invalid value encountered in double_scalars
  return np.dot(a,b)/( np.sqrt(np.sum(a**2.0)) * np.sqrt(np.sum(b**2.0)) )


In [27]:
np.argmax(similarity_vector[1222,:])

0

In [21]:
similarity_vector[1222,1335]

nan

<ipython-input-9-766e32ad4d24>:2: RuntimeWarning: invalid value encountered in double_scalars
  return np.dot(a,b)/( np.sqrt(np.sum(a**2.0)) * np.sqrt(np.sum(b**2.0)) )


In [22]:
similarity_vector = np.nan_to_num(similarity_vector, nan=-1, posinf=-1, neginf=-1)

<ipython-input-9-766e32ad4d24>:2: RuntimeWarning: invalid value encountered in double_scalars
  return np.dot(a,b)/( np.sqrt(np.sum(a**2.0)) * np.sqrt(np.sum(b**2.0)) )


In [38]:
df.loc[2858]

id                                                                    2859
belongs_to_collection    [{'id': 87118, 'name': 'Cars Collection', 'pos...
budget                                                           120000000
genres                   [{'id': 16, 'name': 'Animation'}, {'id': 12, '...
homepage                 http://disney.go.com/disneyvideos/animatedfilm...
imdb_id                                                          tt0317219
original_language                                                       en
original_title                                                        Cars
overview                 [lightning, mcqueen, a, hotshot, rookie, race,...
popularity                                                         18.9079
poster_path                               /5damnMcRFKSjhCirgX3CMa88MBj.jpg
production_companies     [{'name': 'Walt Disney Pictures', 'id': 2}, {'...
production_countries     [{'iso_3166_1': 'US', 'name': 'United States o...
release_date             

<ipython-input-9-766e32ad4d24>:2: RuntimeWarning: invalid value encountered in double_scalars
  return np.dot(a,b)/( np.sqrt(np.sum(a**2.0)) * np.sqrt(np.sum(b**2.0)) )
